In [1]:
import re
import pandas as pd

In [2]:
def get_systemcall_name_with_fork(line):
    syscall = ''
    linelist = line.split(' ')
    pid = int(linelist[0])
    time_cost = re.split('<|>', linelist[-1])

    try:
        time_cost = float(time_cost[1])
    except:
        time_cost = 0
    for i,l in enumerate(linelist):
        if re.match(r'\d{2}:\d{2}:\d{2}', l) is not None:
            timestamp = l
            if '(' in linelist[i+1]:
                syscall = linelist[i+1].split('(')[0]
            elif '<...' in linelist[i+1]:
                syscall = linelist[i+2]
            elif '+++' in linelist[i+1]:
                syscall = linelist[i+2]
            elif '---' in linelist[i+1]:
                syscall = linelist[i+2]
            else:
                syscall = '!!'+linelist[i+1]
            break
    return [pid, timestamp, syscall, time_cost]

In [3]:
def get_systemcall_name_without_fork(line):
    syscall = ''
    linelist = line.split(' ')
    pid = int(linelist[0])
    time_cost = re.split('<|>', linelist[-1])

    try:
        time_cost = float(time_cost[1])
    except:
        time_cost = 0
    for i,l in enumerate(linelist):
        if re.match(r'\d{2}:\d{2}:\d{2}', l) is not None:
            timestamp = l
            if '(' in linelist[i+1]:
                syscall = linelist[i+1].split('(')[0]
            elif '<...' in linelist[i+1]:
                syscall = linelist[i+2]
            elif '+++' in linelist[i+1]:
                syscall = linelist[i+2]
            elif '---' in linelist[i+1]:
                syscall = linelist[i+2]
            else:
                syscall = '!!'+linelist[i+1]
            break
    return [pid, timestamp, syscall, time_cost]

In [58]:
trace = []
with open('systemcalls_demo.txt', 'r') as inputfile:
    for line in inputfile:
        syscall = get_systemcall_name_with_fork(line)
        if syscall[1].startswith('!!'):
            print(line)
        else:
            trace.append(syscall)


In [59]:
trace = pd.DataFrame(trace)[0:1000]

In [60]:
trace.columns = ['pid', 'timestamp', 'syscall', 'timecost']

In [61]:
trace.to_csv('trace_demo.tsv',sep='\t')

In [10]:
def creat_dict(syscall_list):
    feature_dict = list(set(syscall_list))
    feature_dict.append('UNK')
    return feature_dict

In [51]:
def create_onehot_encoding(total, index):
    onehot = []
    for i in range(0, total):
        if i == index:
            onehot.append(1)
        else:
            onehot.append(0)
    return onehot


In [52]:
def read_dict_from_file(dictfilepath):
    syscall_dict = dict()
    syscall_dict_onehot = dict()
    index_dict = dict()
    file_dict = pd.read_csv(dictfilepath,header=None)
    file_dict.columns = ['syscall', 'index']
    syscall = file_dict['syscall']
    index = file_dict['index']
    total = len(syscall)
    for i,sc in enumerate(syscall):
        syscall_dict[sc] = index[i]
        syscall_dict_onehot[sc] = create_onehot_encoding(total, index[i])
        index_dict[index[i]] = sc
    return syscall_dict,syscall_dict_onehot,index_dict



In [53]:
dictfilepath = 'syscalls_to_index.csv'
syscall_dict, syscall_dict_onehot, index_dict = read_dict_from_file(dictfilepath)

In [54]:
syscall_dict_onehot

{'accept': [1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,


In [64]:
def trace_onehot_encoding(trace, syscall_dict_onehot):
    encoded_trace = []
    for syscall in trace['syscall']:
        if syscall in syscall_dict_onehot:
            one_hot = syscall_dict_onehot[syscall]
        else:
            syscall = 'UNK'
            one_hot = syscall_dict_onehot[syscall]
        encoded_trace.append(one_hot)
    return encoded_trace
        

In [66]:
encoded_trace =  trace_onehot_encoding(trace, syscall_dict_onehot)


In [75]:
encoded_trace_df = pd.DataFrame([trace['timestamp'].tolist(), trace['syscall'].tolist(), trace['timecost'].tolist(), encoded_trace]).transpose()

In [76]:

encoded_trace_df.columns=['timestamp', 'syscall', 'timecost', 'one_hot_encoding']

In [78]:
encoded_trace_df.to_csv('one_hot_encoding_features.csv')

In [11]:
feature_dict = creat_dict(trace['syscall'])
feature_dict = pd.DataFrame(feature_dict)
feature_dict.to_csv('1gram_dict.tsv',sep='\t')

In [12]:
import nltk

In [13]:
def get_ngram_trace(syscall_list, n):
    n_gram = list(nltk.ngrams(syscall_list, n))
    return n_gram

In [14]:
n_gram = get_ngram_trace(trace['syscall'], 5)
n_gram

[('wait4', 'rt_sigaction', 'rt_sigprocmask', 'SIGCHLD', 'wait4'),
 ('rt_sigaction', 'rt_sigprocmask', 'SIGCHLD', 'wait4', 'sigreturn'),
 ('rt_sigprocmask', 'SIGCHLD', 'wait4', 'sigreturn', 'rt_sigprocmask'),
 ('SIGCHLD', 'wait4', 'sigreturn', 'rt_sigprocmask', 'rt_sigprocmask'),
 ('wait4', 'sigreturn', 'rt_sigprocmask', 'rt_sigprocmask', 'rt_sigprocmask'),
 ('sigreturn', 'rt_sigprocmask', 'rt_sigprocmask', 'rt_sigprocmask', 'pipe'),
 ('rt_sigprocmask',
  'rt_sigprocmask',
  'rt_sigprocmask',
  'pipe',
  'rt_sigprocmask'),
 ('rt_sigprocmask',
  'rt_sigprocmask',
  'pipe',
  'rt_sigprocmask',
  'rt_sigprocmask'),
 ('rt_sigprocmask',
  'pipe',
  'rt_sigprocmask',
  'rt_sigprocmask',
  'rt_sigprocmask'),
 ('pipe', 'rt_sigprocmask', 'rt_sigprocmask', 'rt_sigprocmask', 'clone'),
 ('rt_sigprocmask',
  'rt_sigprocmask',
  'rt_sigprocmask',
  'clone',
  'rt_sigprocmask'),
 ('rt_sigprocmask',
  'rt_sigprocmask',
  'clone',
  'rt_sigprocmask',
  'rt_sigaction'),
 ('rt_sigprocmask', 'clone', 'rt_s

In [15]:
feature_dict = creat_dict(n_gram)
feature_dict

[('mmap2', 'close', 'open', 'fstat64', 'mmap2'),
 ('getegid32', 'getuid32', 'getgid32', 'access', 'rt_sigaction'),
 ('lseek', 'set_tls', 'lseek', 'read', 'mprotect'),
 ('read', 'lseek', 'read', 'read', 'fstat64'),
 ('open', 'read', 'fstat64', 'read', 'fstat64'),
 ('cacheflush', 'mprotect', 'mprotect', 'mprotect', 'munmap'),
 ('close', 'munmap', 'close', 'munmap', 'access'),
 ('open', 'mmap2', 'open', 'mmap2', 'read'),
 ('mprotect', 'fstat64', 'mmap2', 'fstat64', 'mmap2'),
 ('access', 'mmap2', 'open', 'close', 'open'),
 ('lseek', 'open', 'read', 'open', 'read'),
 ('lseek', 'read', 'lseek', 'lseek', 'read'),
 ('rt_sigprocmask', 'rt_sigprocmask', 'close', 'rt_sigprocmask', 'close'),
 ('open', 'access', 'fstat64', 'access', 'fstat64'),
 ('getuid32', 'access', 'getgid32', 'access', 'getgid32'),
 ('exit_group', 'rt_sigprocmask', 'rt_sigaction', 'wait4', 'exited'),
 ('lseek', 'mprotect', 'read', 'mmap2', 'read'),
 ('read', 'mprotect', 'read', 'mprotect', 'fstat64'),
 ('rt_sigprocmask',
  'rt_

In [16]:
feature_dict = pd.DataFrame(feature_dict)
feature_dict.to_csv('5gram_dict.tsv',sep='\t')

In [17]:
tracestrs = []
s = ''
i = 0
for syscall in trace['syscall'].tolist():
    i += 1
    s += syscall + ' '
    if i == 1000:
        tracestrs.append(s)
        s = ''
        i = 0

In [18]:
from sklearn.feature_extraction.text import TfidfVectorizer
# vectorizer = TfidfVectorizer(ngram_range=(2,2))
vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform(tracestrs)

In [19]:
vectorizer.vocabulary_

{'wait4': 35,
 'rt_sigaction': 24,
 'rt_sigprocmask': 25,
 'sigchld': 29,
 'sigreturn': 30,
 'pipe': 22,
 'clone': 4,
 'close': 5,
 'read': 23,
 'getpid': 15,
 'dup2': 6,
 'stat64': 31,
 'geteuid32': 13,
 'getegid32': 12,
 'getuid32': 16,
 'getgid32': 14,
 'access': 1,
 'execve': 7,
 'brk': 2,
 'uname': 34,
 'mmap2': 18,
 'open': 21,
 'fstat64': 11,
 'lseek': 17,
 'mprotect': 19,
 'munmap': 20,
 'set_tls': 28,
 'cacheflush': 3,
 '_llseek': 0,
 'write': 36,
 'exit_group': 8,
 'exited': 9,
 'fadvise64_64': 10,
 'set_tid_address': 27,
 'set_robust_list': 26,
 'ugetrlimit': 33,
 'statfs': 32}

In [20]:
a = ['wait4',
 'rt_sigaction',
 'rt_sigprocmask',
 'SIGCHLD',
 'wait4',
 'sigreturn',
 'rt_sigprocmask',
 'rt_sigprocmask',
 'rt_sigprocmask']

In [21]:
def get_distance(trace,head,tail):
    start = 0
    end = -1
    distance = 0.0
    for i,s in enumerate(trace):
        if s == head:
            start=i
            rest = trace[i+1:]
            # print(rest)
            if i+1 < len(trace):
                if rest.count(head)>0:
                    end = rest.index(head)+start+1
                    sort = trace[start+1:end]
                    for j,t in enumerate(sort):
                        if t==tail:
                            distance += 1/(j+1)
                else:
                    sort = trace[start+1:]
                    for j,t in enumerate(sort):
                        if t==tail:
                            distance += 1/(j+1)
    return distance

In [22]:
def dependency_graph(trace,term_dict):
    dp = []
    for head in term_dict:
        dp_ = []
        for tail in term_dict:
            if head == tail:
                dp_.append(0)
            else:
                distance = get_distance(trace,head,tail)
                dp_.append(distance)
        dp.append(dp_)
    return dp

In [23]:
feature_dict = creat_dict(trace['syscall'])

In [24]:
st = trace['syscall'].tolist()

In [25]:
dp = dependency_graph(st,feature_dict)

In [26]:
dp

[[0,
  0.26287393339231413,
  0.029411764705882353,
  12.071064340754708,
  3.0419043131265915,
  0.026177973789181484,
  0.010416666666666666,
  0.015070028011204481,
  3.446656383559883,
  7.717389533697579,
  12.874203758209525,
  3.7851124559144886,
  0.008620689655172414,
  4.322113427109869,
  0.02564102564102564,
  16.736901722737418,
  21.47751208885887,
  10.957164389236464,
  7.442857358821438,
  0.010869565217391304,
  0.04706533776301218,
  0.022881245805132004,
  5.683287723736155,
  0.11731466598723236,
  0.7625,
  0.040417529299784094,
  0.16748211220827852,
  0.008928571428571428,
  0.0186932215234102,
  0.02857142857142857,
  8.144317698887164,
  0.08712121212121213,
  2.2889671977962904,
  0.00847457627118644,
  2.798036474661925,
  0.3558663558663559,
  1.8983516483516483,
  0.0],
 [1.8737260007177021,
  0,
  1.0,
  0.19593708720170508,
  1.7821775438904008,
  0.03047803267491078,
  0.013333333333333334,
  0.017956019617149183,
  2.5644572886624437,
  1.0643375700292

In [27]:
pd.DataFrame(dp)

0         1         2          3          4         5         6   \
0    0.000000  0.262874  0.029412  12.071064   3.041904  0.026178  0.010417   
1    1.873726  0.000000  1.000000   0.195937   1.782178  0.030478  0.013333   
2    0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   
3    9.811581  0.097578  0.001698   0.000000   0.368889  0.021228  0.007634   
4    3.520187  3.450000  0.500000   0.194959   0.000000  0.030240  0.013158   
5    0.425086  0.046983  0.001401   2.040192   0.211174  0.000000  0.005650   
6    0.162646  0.018393  0.001255   0.316637   0.103084  0.080456  0.000000   
7    0.353427  0.043619  0.001346   0.984816   0.198775  1.084483  0.005525   
8    3.163164  0.143796  0.002801   0.197924   0.611002  0.030965  0.013699   
9    3.327011  0.572510  0.034483   0.181399  10.659701  0.027085  0.010989   
10   2.453357  0.720044  0.035714   1.013084  15.167670  0.160622  0.333333   
11   7.751941  0.107137  0.001733   7.132278   0.394600  0.021576  0.007812   
12   0.298497  0.040041  0.001287   0.702612   0.185201  0.305026  0.005348   
13   2.073359  0.128637  0.001795   8.735046   0.449288  1.444444  0.008130   
14   0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   
15  11.883434  5.180952  0.045455   0.292244  27.544791  0.064836  0.100000   
16   7.006910  0.548963  0.030303   0.296803   6.231330  0.067381  0.125000   
17  11.165177  1.502047  0.037037   0.314007  10.458943  0.078496  1.000000   
18   2.847685  0.100554  0.001709  11.074266   0.377000  0.021343  0.007692   
19   0.159735  0.018190  0.001248   0.306384   0.102234  0.073239  0.250000   
20   0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   
21   0.580390  0.054052  0.001437   5.506596   0.235667  0.354843  0.006211   
22  12.081944  0.110794  0.001745  10.481672   0.404184  0.021695  0.007874   
23   0.873535  0.082442  0.001792   0.715753   0.309028  0.341346  0.005376   
24   3.889430  0.149822  0.001845   0.159967   0.499547  0.022565  0.008333   
25   0.435591  0.048149  0.001395   1.834719   0.215150  0.443487  0.005814   
26   0.247126  0.643944  0.200000   0.192084   5.411061  0.029550  0.012658   
27   0.175652  0.019255  0.001280   0.366102   0.106643  0.148076  0.000000   
28   0.172176  0.019032  0.001274   0.352257   0.105728  0.119607  0.000000   
29   0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   
30  15.815396  4.656566  0.043478   8.752576   8.712979  0.922222  0.500000   
31   0.244284  0.010989  0.010870   0.000000   0.573229  0.000000  0.000000   
32   2.600586  0.087495  0.001773   7.978392   0.330534  4.500000  0.006329   
33   0.304839  0.040596  0.001290   0.729538   0.187225  0.390036  0.005405   
34   4.723515  0.103733  0.001721   7.309279   0.385556  0.021459  0.007752   
35   0.205281  0.247477  0.047619   0.188382   7.233291  0.028679  0.012048   
36   3.682354  0.136508  0.001818   0.158677   0.467993  0.022309  0.008197   
37   0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   

          7         8          9   ...        28        29         30  \
0   0.015070  3.446656   7.717390  ...  0.018693  0.028571   8.144318   
1   0.017956  2.564457   1.064338  ...  0.023259  0.500000   4.466846   
2   0.000000  0.309524   0.000000  ...  0.000000  1.000000   0.000000   
3   0.011899  0.231830   0.405260  ...  0.014085  0.001695   4.732087   
4   0.017793  1.500515   5.875210  ...  0.022992  0.333333  15.371798   
5   0.042037  0.069483   0.199463  ...  0.010639  0.001399   3.062314   
6   0.061997  0.023758   0.116493  ...  0.183333  0.001253   1.720564   
7   0.000000  0.063880   0.184462  ...  0.010417  0.001344   1.670465   
8   0.018291  0.000000   1.691466  ...  0.023813  0.002793   2.193365   
9   0.015668  0.309297   0.000000  ...  0.019610  0.033333  11.774880   
10  0.126984  2.293116  32.733333  ...  0.342857  0.034483  26.575405   
11  0.012117  0.311639   0.450972  ...  0.014389  0.0

In [28]:
pd.to_pickle(dp,'dependency_graph.pkl')

In [31]:
d = pd.DataFrame(pd.read_pickle('dependency_graph.pkl'))

In [32]:
d

0         1         2          3          4         5         6   \
0    0.000000  0.262874  0.029412  12.071064   3.041904  0.026178  0.010417   
1    1.873726  0.000000  1.000000   0.195937   1.782178  0.030478  0.013333   
2    0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   
3    9.811581  0.097578  0.001698   0.000000   0.368889  0.021228  0.007634   
4    3.520187  3.450000  0.500000   0.194959   0.000000  0.030240  0.013158   
5    0.425086  0.046983  0.001401   2.040192   0.211174  0.000000  0.005650   
6    0.162646  0.018393  0.001255   0.316637   0.103084  0.080456  0.000000   
7    0.353427  0.043619  0.001346   0.984816   0.198775  1.084483  0.005525   
8    3.163164  0.143796  0.002801   0.197924   0.611002  0.030965  0.013699   
9    3.327011  0.572510  0.034483   0.181399  10.659701  0.027085  0.010989   
10   2.453357  0.720044  0.035714   1.013084  15.167670  0.160622  0.333333   
11   7.751941  0.107137  0.001733   7.132278   0.394600  0.021576  0.007812   
12   0.298497  0.040041  0.001287   0.702612   0.185201  0.305026  0.005348   
13   2.073359  0.128637  0.001795   8.735046   0.449288  1.444444  0.008130   
14   0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   
15  11.883434  5.180952  0.045455   0.292244  27.544791  0.064836  0.100000   
16   7.006910  0.548963  0.030303   0.296803   6.231330  0.067381  0.125000   
17  11.165177  1.502047  0.037037   0.314007  10.458943  0.078496  1.000000   
18   2.847685  0.100554  0.001709  11.074266   0.377000  0.021343  0.007692   
19   0.159735  0.018190  0.001248   0.306384   0.102234  0.073239  0.250000   
20   0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   
21   0.580390  0.054052  0.001437   5.506596   0.235667  0.354843  0.006211   
22  12.081944  0.110794  0.001745  10.481672   0.404184  0.021695  0.007874   
23   0.873535  0.082442  0.001792   0.715753   0.309028  0.341346  0.005376   
24   3.889430  0.149822  0.001845   0.159967   0.499547  0.022565  0.008333   
25   0.435591  0.048149  0.001395   1.834719   0.215150  0.443487  0.005814   
26   0.247126  0.643944  0.200000   0.192084   5.411061  0.029550  0.012658   
27   0.175652  0.019255  0.001280   0.366102   0.106643  0.148076  0.000000   
28   0.172176  0.019032  0.001274   0.352257   0.105728  0.119607  0.000000   
29   0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   
30  15.815396  4.656566  0.043478   8.752576   8.712979  0.922222  0.500000   
31   0.244284  0.010989  0.010870   0.000000   0.573229  0.000000  0.000000   
32   2.600586  0.087495  0.001773   7.978392   0.330534  4.500000  0.006329   
33   0.304839  0.040596  0.001290   0.729538   0.187225  0.390036  0.005405   
34   4.723515  0.103733  0.001721   7.309279   0.385556  0.021459  0.007752   
35   0.205281  0.247477  0.047619   0.188382   7.233291  0.028679  0.012048   
36   3.682354  0.136508  0.001818   0.158677   0.467993  0.022309  0.008197   
37   0.000000  0.000000  0.000000   0.000000   0.000000  0.000000  0.000000   

          7         8          9   ...        28        29         30  \
0   0.015070  3.446656   7.717390  ...  0.018693  0.028571   8.144318   
1   0.017956  2.564457   1.064338  ...  0.023259  0.500000   4.466846   
2   0.000000  0.309524   0.000000  ...  0.000000  1.000000   0.000000   
3   0.011899  0.231830   0.405260  ...  0.014085  0.001695   4.732087   
4   0.017793  1.500515   5.875210  ...  0.022992  0.333333  15.371798   
5   0.042037  0.069483   0.199463  ...  0.010639  0.001399   3.062314   
6   0.061997  0.023758   0.116493  ...  0.183333  0.001253   1.720564   
7   0.000000  0.063880   0.184462  ...  0.010417  0.001344   1.670465   
8   0.018291  0.000000   1.691466  ...  0.023813  0.002793   2.193365   
9   0.015668  0.309297   0.000000  ...  0.019610  0.033333  11.774880   
10  0.126984  2.293116  32.733333  ...  0.342857  0.034483  26.575405   
11  0.012117  0.311639   0.450972  ...  0.014389  0.0

In [10]:
from sklearn.feature_extraction.text import TfidfVectorizer
corpus = ['this is the first document',
           'this document is the second document',
           'and this is the third one',
           'is this the first document']

In [11]:
vocabulary = ['this', 'document', 'first', 'is', 'second', 'the',
               'and', 'one']

In [31]:
vectorizer = TfidfVectorizer()
X = vectorizer.fit(corpus)

In [32]:
a = X.transform(['this tfasf faefeg'])

In [33]:
b = a.toarray()
b

array([[0., 0., 0., 0., 0., 0., 0., 0., 1.]])

In [36]:
X.vocabulary_

{'this': 8,
 'is': 3,
 'the': 6,
 'first': 2,
 'document': 1,
 'second': 5,
 'and': 0,
 'third': 7,
 'one': 4}